In [1]:
import librosa
import numpy as np
import matplotlib.pyplot as plt

import os
import numpy as np
import tensorflow as tf
import random
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.utils import to_categorical

import tensorflow as tf
import tensorflow_hub as hub
from tensorflow.keras import layers, models, optimizers, regularizers
from tensorflow.keras import Model

In [2]:
vggish_model = hub.load('https://kaggle.com/models/google/vggish/frameworks/TensorFlow2/variations/vggish/versions/1')

In [3]:
def load_and_preprocess_audio(file_path, target_duration=30, target_sr=16000):
    # Load audio file with original sampling rate
    audio, sr = librosa.load(file_path, sr=None)
    
    # Resample if needed
    if sr != target_sr:
        audio = librosa.resample(y=audio, orig_sr=sr, target_sr=target_sr)
        sr = target_sr
    
    # Ensure target duration
    target_length = int(sr * target_duration)
    if len(audio) < target_length:
        audio = np.pad(audio, (0, target_length - len(audio)))
    elif len(audio) > target_length:
        audio = audio[:target_length]
    
    
    # Run the model, check the output.
    embeddings = vggish_model(audio)
    embeddings.shape.assert_is_compatible_with([None, 128])
    return embeddings

In [5]:
# dataset_path = os.path.join('ROBOVOX_SP_CUP_2024', 'data', 'single-channel', 'dataset')
dataset_path = "C:/Users/nidul/Desktop/ACCA Folder My/Signal processing cup/ROBOVOX_SP_CUP_2024/single-channel/enrollment"
speakers = os.listdir(dataset_path)

In [9]:
embeddings = []
labels = []

file_paths = []
for filename in speakers:
    for files in os.listdir(os.path.join(dataset_path, filename)):
        file_path = os.path.join(dataset_path, filename,files)
        embedding = load_and_preprocess_audio(file_path)
        embeddings.append(embedding)
        labels.append(filename)
print(embedding)

tf.Tensor(
[[ 0.20242427 -0.1331912   0.07179558 ...  0.18894994  0.1841952
  -0.61777455]
 [ 0.09878142  0.1388015   0.14522639 ...  0.40458262  0.06088639
  -0.28442538]
 [ 0.21000457 -0.5211786   0.3551849  ... -0.6666522   0.3612811
  -0.6151622 ]
 ...
 [-0.26968613 -0.05457264 -0.1370081  ... -0.16206095  0.22875692
   0.17773895]
 [-0.26968613 -0.05457264 -0.1370081  ... -0.16206095  0.22875692
   0.17773895]
 [-0.26968613 -0.05457264 -0.1370081  ... -0.16206095  0.22875692
   0.17773895]], shape=(31, 128), dtype=float32)


In [10]:
len(embeddings)

225

In [11]:
embeddings[0].shape

TensorShape([31, 128])

In [12]:
#Now let's wirte denoised .wav files in a new folder (New folder I named as denoise audio)
denoised_folder = "C:/Users/nidul/Desktop/ACCA Folder My/Signal processing cup/ROBOVOX_SP_CUP_2024/single-channel/denoised"
denoised_labels = os.listdir(denoised_folder)

In [13]:
test_embeddings = []
test_labels = []

test_file_paths = []
for i, filename in enumerate(denoised_labels):
    file_path = os.path.join(denoised_folder, filename)
    embedding = load_and_preprocess_audio(file_path)
    test_embeddings.append(embedding)
    test_labels.append(filename[:-4])
    print(f"File {i} : {filename} embedding generated")

File 0 : 0000f88619.wav embedding generated
File 1 : 000f6d0072.wav embedding generated
File 2 : 001dd0cb47.wav embedding generated
File 3 : 001f7db31a.wav embedding generated
File 4 : 001f86a5bf.wav embedding generated
File 5 : 002724b7ea.wav embedding generated
File 6 : 0042734703.wav embedding generated
File 7 : 00465a38b0.wav embedding generated
File 8 : 004adba134.wav embedding generated
File 9 : 005ae9cb2b.wav embedding generated
File 10 : 006a19dfc1.wav embedding generated
File 11 : 006ce8656f.wav embedding generated
File 12 : 00806ad24b.wav embedding generated
File 13 : 0086c2506c.wav embedding generated
File 14 : 008a2d1b07.wav embedding generated
File 15 : 008a7764f2.wav embedding generated
File 16 : 0094b5dfc9.wav embedding generated
File 17 : 009ba16c1a.wav embedding generated
File 18 : 00a49d6b07.wav embedding generated
File 19 : 00a794c50e.wav embedding generated
File 20 : 00a931d755.wav embedding generated
File 21 : 00a99c3526.wav embedding generated
File 22 : 00b83bd14a

In [14]:
from sklearn.metrics.pairwise import cosine_similarity

In [150]:
file_path = "C:/Users/nidul/Desktop/ACCA Folder My/Signal processing cup/ROBOVOX_SP_CUP_2024/single-channel/signle-channel-trials.trl"

with open(file_path, 'r') as file:
    for line in file:
        speaker = line.split()[0]
        sample = line.split()[1]
        for i, label in enumerate(labels):
            if label == speaker:
                speaker_index = i
                break  # Break the loop once a match is found
        for i, label in enumerate(test_labels):
            if label == sample:
                index = i
                break  # Break the loop once a match is found
        test_array = test_embeddings[index]
        speaker_array = embeddings[speaker_index]
        array1_2d = tf.reshape(test_array, (1, -1))
        array2_2d = tf.reshape(speaker_array, (1, -1))
        similarity = cosine_similarity(array1_2d, array2_2d)
        print(speaker,"/t", sample, "/t", similarity[0][0])

spk_71  b80bb95d16  0.37371457
spk_71  e64da37b33  0.42446285
spk_71  c22d8f9d8a  0.4016202
spk_71  20e087d5bf  0.39192104
spk_71  c5396d4af7  0.38856208
spk_71  07e622c018  0.43109506
spk_71  70d3397783  0.39511567
spk_71  e967199344  0.44923463
spk_71  35e670b698  0.38290006
spk_71  6d80d0d2a1  0.41280314
spk_71  97bbaeadba  0.398386
spk_71  a62faf1119  0.43473727
spk_71  34ceda1014  0.4145729
spk_71  33e5a6f028  0.40341777
spk_71  bf3c182f9a  0.41256648
spk_71  e350f7e8d3  0.36608544
spk_71  16a0dfa929  0.4152068
spk_71  0c5875ee78  0.3976099
spk_71  b965a8584d  0.39450967
spk_71  3bb3d70992  0.41179103
spk_71  28283fdfe9  0.4175511
spk_71  c32b02c633  0.41513282
spk_71  9f6008448e  0.4380778
spk_71  c399f9f4b9  0.40048423
spk_71  4a13ea812b  0.41239563
spk_71  6921397f4e  0.3978327
spk_71  615afd399e  0.43887854
spk_71  6a9bf1b286  0.41356415
spk_71  0f6fcf528a  0.40820396
spk_71  96cec5103b  0.40970194
spk_71  782e9b8523  0.4068994
spk_71  a1dda7f0e2  0.40471786
spk_71  a08d312960

In [151]:
type(test_embeddings[0])

tensorflow.python.framework.ops.EagerTensor

In [152]:
array1 = test_embeddings[0]
array2 = embeddings[0]
array1_2d = tf.reshape(array1, (1, -1))
array2_2d = tf.reshape(array2, (1, -1))
similarity = cosine_similarity(array1_2d, array2_2d)


In [153]:
similarity

array([[0.5140271]], dtype=float32)

In [154]:
from sklearn.decomposition import FactorAnalysis

In [155]:
# Convert embeddings to NumPy arrays
embeddings_np = np.array([embedding.numpy() for embedding in embeddings])
# Reshape to (num_samples * num_features, num_dimensions)
embeddings_flattened = embeddings_np.reshape(embeddings_np.shape[0], -1)

# Apply Factor Analysis
fa = FactorAnalysis(n_components=1)
ivectors = fa.fit_transform(embeddings_flattened)

In [156]:
import librosa

def get_audio_duration(file_path):
    time = []
    for file in os.listdir(file_path):
    # Load the audio file
        path = os.path.join(file_path, file)
        audio, sr = librosa.load(path, sr=None)
    
    # Calculate the duration in seconds
        duration = librosa.get_duration(y=audio, sr=sr)
        time.append(duration)
    return time

# Example usage
file_path = dataset_path
duration = get_audio_duration(file_path)
print(max(duration))


48.0371875
